## Document Embedding and Clustering Pipeline - Exploration
# This notebook outlines the steps to cluster documents based on their semantic embeddings
# and visualize the results.


#
# ## Step 1: Load and Inspect Existing Data
#
# First, let's connect to the database and load a sample of the data from the
# `summary_vectors` table to understand its current state.

In [80]:


# %%
import sys
import time
import pandas as pd
import numpy as np
from sqlalchemy import text
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
SAMPLE_SIZE = 100 # How many rows to fetch for initial inspection

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")
    # Optionally, exit or raise error if essential
    # sys.exit("Stopping notebook execution.")

# --- Connect and Fetch Sample Data ---
df_sample = pd.DataFrame() # Initialize empty DataFrame
session = None
engine = None

print(f"\nConnecting to database and fetching {SAMPLE_SIZE} sample rows...")
fetch_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - fetch_start_time:.2f}s")

        # Fetch a sample of all relevant columns
        # Using LIMIT for sampling. For larger tables, consider TABLESAMPLE if supported/needed.
        query = text(f"""
            SELECT
              doc_id,
              summary,
              embedding,
              cluster_id,
              cluster_label,
              file_path,
              cluster_name
            FROM public.summary_vectors
            ORDER BY doc_id -- Or RANDOM() if performance allows and true random sample needed
            LIMIT :limit;
        """)

        df_sample = pd.read_sql(query, con=engine, params={'limit': SAMPLE_SIZE})
        print(f"   Fetched {len(df_sample)} rows in {time.time() - fetch_start_time:.2f}s total.")

        # --- Basic Data Inspection ---
        print("\n--- Sample Data Head ---")
        display(df_sample.head()) # display() is preferred in notebooks

        print("\n--- DataFrame Info ---")
        # Use buffer to capture info output for printing if needed, or rely on notebook display
        # import io
        # buffer = io.StringIO()
        # df_sample.info(buf=buffer)
        # print(buffer.getvalue())
        df_sample.info() # In notebooks, this usually prints directly

        print("\n--- Descriptive Statistics (including non-numeric) ---")
        display(df_sample.describe(include='all'))

        # --- Check Embedding Format ---
        if not df_sample.empty and 'embedding' in df_sample.columns:
            first_embedding = df_sample['embedding'].iloc[0]
            print(f"\n--- Sample Embedding (Type: {type(first_embedding)}) ---")
            if isinstance(first_embedding, (np.ndarray, list)):
                 print(f"   Length: {len(first_embedding)}")
                 print(f"   Preview: {str(first_embedding)[:50]}...{str(first_embedding)[-50:]}")
            elif isinstance(first_embedding, str):
                 print(f"   Preview (string): {first_embedding[:50]}...{first_embedding[-50:]}")
                 print("   ⚠️ Embeddings seem to be stored as strings. Parsing will be needed.")
            else:
                 print(f"   Value: {first_embedding}")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ Error during database connection or data fetching: {e}")

finally:
    # --- Close Connection ---
    if session:
        session.close()
        print("\nDatabase session closed.")




✅ init_vector_db imported successfully.

Connecting to database and fetching 100 sample rows...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

❌ Error during database connection or data fetching: (psycopg2.errors.UndefinedColumn) column "cluster_label" does not exist
LINE 7:               cluster_label,
                      ^
HINT:  Perhaps you meant to reference the column "summary_vectors.cluster_name".

[SQL: 
            SELECT
              doc_id,
              summary,
              embedding,
              cluster_id,
              cluster_label,
              file_path,
              cluster_name
            FROM public.summary_vectors
            ORDER BY doc_id -- Or RANDOM() if performance allows and true random sample needed
            LIMIT %(limit)s;
        ]
[parameters: {'limit': 100}]
(Background on this error at: https://sqlalche.me/e/20/f405)

Database session closed.


# ## Step 2: Clear Existing Data (Optional)
#
# **⚠️ WARNING: Running this cell (after uncommenting the execution line) will permanently delete all data from the `public.summary_vectors` table.**
#
# Only proceed if you intend to start the population process from scratch.


In [81]:

import sys
import time
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Drop Table ---
session = None
engine = None
action_performed = False # Flag to track if modification was attempted

print("\nConnecting to database to potentially DROP table...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        inspector = sql_inspect(engine) # Create inspector to check if table exists
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # Check if table exists before trying to drop it
        if inspector.has_table("summary_vectors", schema="public"):
            print("   Table 'public.summary_vectors' exists.")

            # --- !!! DANGER ZONE !!! ---
            # --- Uncomment the next two lines only if you are absolutely certain ---
            # --- you want to DROP the entire table. ---

            print("   Executing DROP TABLE public.summary_vectors;")
            session.execute(text("DROP TABLE public.summary_vectors CASCADE;")) # Use CASCADE to drop dependent objects like indexes
            action_performed = True # Set flag if uncommented

        else:
            print("   Table 'public.summary_vectors' does not exist, skipping drop command.")


        # --- Commit Transaction ONLY if an action was performed ---
        if action_performed:
             print("\n   Committing changes...")
             session.commit()
             print("   ✅ Changes committed. Table dropped.")
        else:
             print("\n   Skipped table drop (command is commented out or table didn't exist).")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ Error during database connection or table drop: {e}")
    if session:
        print("   Rolling back transaction due to error.")
        session.rollback() # Rollback in case of error during drop attempt
finally:
    # --- Close Connection ---
    if session:
        session.close()
        print("\nDatabase session closed.")

if action_performed:
    print("\n✅ Table drop attempt finished.")
else:
    print("\nℹ️ Table was not dropped (command commented out or table didn't exist).")

# %% [markdown]
# ## Next Steps
#
# If you uncommented and ran the `DROP TABLE` command:
# 1. The `summary_vectors` table no longer exists.
# 2. You **must** run your table creation script (e.g., `create_summary_table_simple.py`) before you can proceed with loading any data into a table named `summary_vectors`.
#
# If you kept the command commented out:
# 1. The table remains as it was. Proceed accordingly.



✅ init_vector_db imported successfully.

Connecting to database to potentially DROP table...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s
   Table 'public.summary_vectors' exists.
   Executing DROP TABLE public.summary_vectors;

   Committing changes...
   ✅ Changes committed. Table dropped.

Database session closed.

✅ Table drop attempt finished.


### Step 3: Inspect Table State After Modifications
#
# This cell connects to the database and inspects the current state of the
# `public.summary_vectors` table, showing the remaining columns, row count,
# and a sample record based on the current structure.



In [82]:

import sys
import time
import pandas as pd
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
SAMPLE_SIZE = 10 # How many rows to fetch for sample display

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Inspect Table ---
session = None
engine = None
table_exists = False
row_count = 0
existing_columns = []

print("\nConnecting to database to inspect 'summary_vectors' table...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        inspector = sql_inspect(engine)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Check Table Existence ---
        print("\n[1/3] Checking table existence...")
        if inspector.has_table("summary_vectors", schema="public"):
             table_exists = True
             print("   ✅ Table 'public.summary_vectors' exists.")
        else:
             print("   ❌ Table 'public.summary_vectors' does not exist.")
             session.close() # No need to proceed if table doesn't exist
             # sys.exit("Stopping - table not found.") # Use if stopping execution is desired

        if table_exists:
            # --- 2) Inspect Schema (Current Columns) ---
            print("\n[2/3] Inspecting current table schema...")
            try:
                columns_info = inspector.get_columns("summary_vectors", schema="public")
                print("   🗒️  Columns currently in table:")
                if columns_info:
                    for column in columns_info:
                        col_name = column['name']
                        col_type = str(column['type'])
                        col_nullable = column['nullable']
                        existing_columns.append(col_name) # Store existing column names
                        print(f"      • {col_name:<15} {col_type:<20} {'NULLABLE' if col_nullable else 'NOT NULL'}")
                else:
                    print("      No columns found (this is unexpected if table exists).")
            except Exception as e:
                print(f"   ⚠️ Error inspecting schema: {e}")

            # --- 3) Fetch Row Count and Sample Data ---
            print("\n[3/3] Fetching row count and sample data...")
            try:
                # Get row count
                count_result = session.execute(
                     text("SELECT COUNT(*) FROM public.summary_vectors;")
                 ).scalar_one_or_none()
                row_count = count_result if count_result is not None else 0
                print(f"   📊 Current row count: {row_count}")

                # Fetch sample data only if table is not empty and columns exist
                if row_count > 0 and existing_columns:
                    select_cols_str = ", ".join([f'"{col}"' for col in existing_columns]) # Quote column names
                    sample_query = text(f"""
                        SELECT {select_cols_str}
                        FROM public.summary_vectors
                        ORDER BY doc_id -- Or RANDOM()
                        LIMIT :limit;
                    """)
                    df_sample = pd.read_sql(sample_query, con=engine, params={'limit': SAMPLE_SIZE})
                    print(f"\n   📄 Sample data ({len(df_sample)} rows):")
                    display(df_sample) # Display DataFrame in notebook
                elif row_count == 0:
                     print("   ℹ️ Table is empty, cannot fetch sample data.")
                else:
                     print("   ℹ️ No columns found, cannot fetch sample data.")

            except Exception as e:
                print(f"   ⚠️ Error fetching count or sample data: {e}")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred: {e}")
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")
    elif not table_exists and 'init_vector_db' in globals():
         print("\nDatabase session closed (or not needed as table didn't exist).")


print(f"\n✅ Inspection finished.")




✅ init_vector_db imported successfully.

Connecting to database to inspect 'summary_vectors' table...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.02s

[1/3] Checking table existence...
   ❌ Table 'public.summary_vectors' does not exist.

Database session closed.

✅ Inspection finished.


In [83]:
# %% [markdown]
# ## Step 1: Simple Inspection of Source JSON Data
#
# Load the source JSON file and display basic information about its structure
# and a few sample records.

# %%
import json
import warnings

# --- Configuration ---
# Path to the source JSON file
JSON_PATH = "/shared_folders/team_1/ben/10000_summaries.json" #<-- Verify this path
SAMPLE_DISPLAY_COUNT = 3 # How many records to print as a sample

# --- Load and Inspect JSON ---
raw_data = None

print(f"Attempting to load JSON data from: {JSON_PATH}")

try:
    with open(JSON_PATH, "r") as f:
        raw_data = json.load(f)
    print("✅ JSON data loaded successfully.")

    # --- Print Basic Info ---
    data_type = type(raw_data).__name__
    print(f"\n--- Basic Info ---")
    print(f"Data Type: {data_type}")

    if isinstance(raw_data, (dict, list)):
        record_count = len(raw_data)
        print(f"Number of Records: {record_count}")

        print(f"\n--- First {SAMPLE_DISPLAY_COUNT} Records (Structure Preview) ---")
        if isinstance(raw_data, dict):
            count = 0
            for key, value in raw_data.items():
                if count < SAMPLE_DISPLAY_COUNT:
                    print(f"\nRecord Key: {key}")
                    print(f"Value Type: {type(value).__name__}")
                    print(f"Value Preview: {str(value)[:200]}...") # Show preview
                    count += 1
                else:
                    break
        elif isinstance(raw_data, list):
            for i, item in enumerate(raw_data[:SAMPLE_DISPLAY_COUNT]):
                 print(f"\nRecord Index: {i}")
                 print(f"Value Type: {type(item).__name__}")
                 print(f"Value Preview: {str(item)[:200]}...") # Show preview

    else:
        # Handle other data types if necessary
        print(f"Data Preview: {str(raw_data)[:200]}...")


except FileNotFoundError:
    warnings.warn(f"⚠️ Error: JSON file not found at {JSON_PATH}. Please verify the path.")
except json.JSONDecodeError as e:
     warnings.warn(f"⚠️ Error: Failed to decode JSON from {JSON_PATH}. Check file content: {e}")
except Exception as e:
    warnings.warn(f"⚠️ An unexpected error occurred: {e}")

# %% [markdown]
# ## Next Steps
#
# 1. Review the output to understand the basic structure (dictionary or list) and the content of the first few records.
# 2. Proceed to define the database table schema based on this structure.



Attempting to load JSON data from: /shared_folders/team_1/ben/10000_summaries.json
✅ JSON data loaded successfully.

--- Basic Info ---
Data Type: dict
Number of Records: 9746

--- First 3 Records (Structure Preview) ---

Record Key: 3
Value Type: dict
Value Preview: {'file_path': '/data/projects/filefindr/UTILS/TechTeam/8000 WWTP/Equipment/Degremont/WWTP/WWTPdescription/WWTP Description.docx', 'summary': 'This document describes the wastewater treatment plant (WW...

Record Key: 4
Value Type: dict
Value Preview: {'file_path': '/data/projects/filefindr/UTILS/TechTeam/8000 WWTP/Equipment/Degremont/WWTP/Service Level Agreement/Units service Level agreement.docx', 'summary': 'This document provides a detailed lis...

Record Key: 5
Value Type: dict
Value Preview: {'file_path': '/data/projects/filefindr/UTILS/TechTeam/8000 WWTP/Equipment/Degremont/WWTP/P&ID/0175-SWT-A2-AA0-910 GENERAL NOTES AND SYMBOLS.pdf', 'summary': 'This document is a controlled copy of "01...


In [84]:
# %% [markdown]
# ## Step 2: Define and Create Table Schema
#
# Based on the inspection of the source JSON, this cell defines and creates the
# `public.summary_vectors` table schema.
#
# Columns:
# - `doc_id` (Primary Key, from JSON keys)
# - `summary` (from nested dictionary)
# - `file_path` (from nested dictionary)
# - `embedding` (to be generated later)
# - `cluster_id` (numerical ID for later clustering)
# - `cluster_name` (descriptive name for later clustering)
#
# It uses `IF NOT EXISTS` clauses, making it safe to run multiple times.

# %%
import sys
import time
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
EMBEDDING_DIMENSION = 384 # Dimension of your embeddings (adjust if different)

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Create Table/Index ---
session = None
engine = None
action_performed = False # Flag to track if modification was attempted

print("\nConnecting to database to create/verify table structure...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Create Table ---
        print("\n   Executing CREATE TABLE IF NOT EXISTS...")
        # Define the table schema based on JSON structure and desired columns
        create_table_sql = text(f"""
        CREATE TABLE IF NOT EXISTS public.summary_vectors (
            doc_id        INT PRIMARY KEY,
            summary       TEXT,
            file_path     TEXT,        -- From JSON value dict
            embedding     VECTOR({EMBEDDING_DIMENSION}), -- To be populated
            cluster_id    INT,         -- Numerical ID from clustering (NULLable)
            cluster_name  TEXT         -- Descriptive name for cluster group (NULLable)
        );
        """)
        session.execute(create_table_sql)
        action_performed = True # Assume action attempted, commit needed
        print("      CREATE TABLE command executed.")

        # --- 2) Create pgvector Index ---
        # This creates an index on the embedding column for faster similarity searches later.
        print("\n   Executing CREATE INDEX IF NOT EXISTS...")
        # Using ivfflat index. Consider HNSW depending on pgvector version and needs.
        create_index_sql = text("""
        CREATE INDEX IF NOT EXISTS summary_vec_idx
        ON public.summary_vectors USING ivfflat (embedding vector_cosine_ops);
        """)
        session.execute(create_index_sql)
        print("      CREATE INDEX command executed.")

        # --- Commit Transaction ---
        print("\n   Committing changes...")
        session.commit()
        print("   ✅ Changes committed. Table and index should now exist with the correct schema.")

    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ Error during database connection or table/index creation: {e}")
    if session:
        print("   Rolling back transaction due to error.")
        session.rollback() # Rollback in case of error
finally:
    # --- Close Connection ---
    if session:
        session.close()
        print("\nDatabase session closed.")

if action_performed:
    print("\n✅ Table and index creation attempt finished.")
else:
    print("\nℹ️ Database connection skipped.")

# %% [markdown]
# ## Next Steps
#
# 1. The `summary_vectors` table structure is now defined in the database.
# 2. Proceed to Step 3: Load the basic data (`doc_id`, `summary`, `file_path`) from the JSON file into this table.



✅ init_vector_db imported successfully.

Connecting to database to create/verify table structure...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

   Executing CREATE TABLE IF NOT EXISTS...
      CREATE TABLE command executed.

   Executing CREATE INDEX IF NOT EXISTS...
      CREATE INDEX command executed.

   Committing changes...
   ✅ Changes committed. Table and index should now exist with the correct schema.

Database session closed.

✅ Table and index creation attempt finished.


In [85]:
# %% [markdown]
# ## Step 3: Load Basic Data into `summary_vectors`
#
# This cell loads data from the source JSON file (`10000_summaries.json`).
# For each record, it extracts the `doc_id`, `summary`, and `file_path`.
# It then inserts or updates these values into the `public.summary_vectors` table.
#
# The `embedding`, `cluster_id`, and `cluster_name` columns are intentionally
# left as `NULL` at this stage.

# %%
import sys
import time
import json
from sqlalchemy import text
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
JSON_PATH = "/shared_folders/team_1/ben/10000_summaries.json" #<-- Verify this path
BATCH_SIZE = 500 # Process records in batches for efficiency

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Load JSON Data ---
raw_data = None
print(f"\nLoading JSON data from: {JSON_PATH}")
try:
    with open(JSON_PATH, "r") as f:
        raw_data = json.load(f)
    # Basic validation of loaded data structure
    if not isinstance(raw_data, dict):
        raise TypeError(f"Expected JSON data to be a dictionary, but got {type(raw_data).__name__}")
    print(f"✅ Loaded {len(raw_data)} records from JSON.")
except FileNotFoundError:
    warnings.warn(f"⚠️ Error: JSON file not found at {JSON_PATH}. Cannot proceed.")
    raw_data = None # Ensure raw_data is None if file not found
except (json.JSONDecodeError, TypeError) as e:
     warnings.warn(f"⚠️ Error: Failed to load or validate JSON from {JSON_PATH}. Check file content/format: {e}")
     raw_data = None
except Exception as e:
    warnings.warn(f"⚠️ An unexpected error occurred during JSON loading: {e}")
    raw_data = None

# --- Define Batch Upsert Function ---
def upsert_basic_data_batch(session, batch):
    """
    Inserts or updates a batch of records into the summary_vectors table.
    Only populates doc_id, summary, and file_path.
    Leaves embedding, cluster_id, cluster_name as NULL on insert.
    Updates only summary and file_path on conflict to avoid overwriting potential future data.
    """
    # SQL statement for upserting basic info
    sql = text("""
    INSERT INTO public.summary_vectors
      (doc_id, summary, file_path, embedding, cluster_id, cluster_name)
    VALUES
      (:doc_id, :summary, :file_path, NULL, NULL, NULL)
    ON CONFLICT (doc_id) DO UPDATE
      SET summary   = EXCLUDED.summary,
          file_path = EXCLUDED.file_path;
    """)
    try:
        # Execute the upsert for the entire batch
        session.execute(sql, batch)
        session.commit() # Commit after each successful batch
    except Exception as e:
        warnings.warn(f"⚠️ Error during batch upsert: {e}")
        session.rollback() # Rollback the failed batch
        raise # Re-raise the exception to potentially stop processing

# --- Connect and Load Data into DB ---
session = None
engine = None

# Proceed only if JSON data was loaded successfully and init_vector_db is available
if raw_data is not None and 'init_vector_db' in globals():
    print("\nConnecting to database to load basic data...")
    connect_start_time = time.time()
    try:
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        docs_batch = [] # List to hold records for the current batch
        total_processed = 0
        skipped_records = 0
        batch_start_time = time.time() # Timer for batch processing

        print(f"\nProcessing {len(raw_data)} records from JSON in batches of {BATCH_SIZE}...")
        # Iterate through the JSON dictionary (doc_id_str: record_dict)
        for i, (doc_id_str, record_dict) in enumerate(raw_data.items(), 1):
            try:
                # Validate record structure and content
                if not isinstance(record_dict, dict):
                    warnings.warn(f"Skipping record with key '{doc_id_str}': value is not a dictionary.")
                    skipped_records += 1
                    continue

                # Prepare data dictionary for the current record, converting doc_id
                data_for_db = {
                    "doc_id": int(doc_id_str), # Convert JSON key string to int
                    "summary": record_dict.get("summary"), # Use .get for safety
                    "file_path": record_dict.get("file_path")
                }

                # Basic validation for required fields
                if data_for_db["summary"] is None or data_for_db["file_path"] is None:
                     warnings.warn(f"Skipping doc_id {doc_id_str}: missing 'summary' or 'file_path' key in JSON record value.")
                     skipped_records += 1
                     continue # Skip this record

                # Add the prepared data to the current batch
                docs_batch.append(data_for_db)

                # When batch is full or it's the last item, upsert it
                if len(docs_batch) >= BATCH_SIZE or i == len(raw_data):
                    if docs_batch: # Ensure batch is not empty
                        upsert_basic_data_batch(session, docs_batch)
                        total_processed += len(docs_batch)
                        print(f"  Processed batch ending at record {i}. Total processed: {total_processed}. Time: {time.time() - batch_start_time:.2f}s")
                        docs_batch = [] # Reset batch
                        batch_start_time = time.time() # Reset timer for next batch

            except ValueError:
                warnings.warn(f"Skipping record: Invalid doc_id '{doc_id_str}'. Must be convertible to an integer.")
                skipped_records += 1
            except Exception as e:
                 # Catch potential errors during processing of a single record
                 warnings.warn(f"Skipping record with doc_id '{doc_id_str}' due to error during preparation: {e}")
                 skipped_records += 1


        print("\n--------------------")
        print(f"✅ Basic data loading finished.")
        print(f"   Total records processed and upserted: {total_processed}")
        if skipped_records > 0:
            print(f"   Total records skipped due to errors or missing data: {skipped_records}")
        print("--------------------")


    except Exception as e:
        # Catch errors during connection or the main loop setup
        print(f"\n❌ An error occurred during the main data loading process: {e}")
    finally:
        # --- Close Connection ---
        if session:
            session.close()
            print("\nDatabase session closed.")

elif raw_data is None:
     print("\nSkipping database loading because JSON data could not be loaded or validated.")
else:
     print("\nSkipping database loading because init_vector_db could not be imported.")


# %% [markdown]
# ## Next Steps
#
# 1. The `summary_vectors` table should now be populated with `doc_id`, `summary`, and `file_path` for all valid records from the JSON file. The other columns (`embedding`, `cluster_id`, `cluster_name`) should be `NULL`.
# 2. You can run the verification script/cell next to confirm this.
# 3. The next logical step after verification is to generate the embeddings for the summaries and update the `embedding` column in the table.



✅ init_vector_db imported successfully.

Loading JSON data from: /shared_folders/team_1/ben/10000_summaries.json
✅ Loaded 9746 records from JSON.

Connecting to database to load basic data...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

Processing 9746 records from JSON in batches of 500...
  Processed batch ending at record 500. Total processed: 500. Time: 0.05s
  Processed batch ending at record 1000. Total processed: 1000. Time: 0.04s
  Processed batch ending at record 1500. Total processed: 1500. Time: 0.04s
  Processed batch ending at record 2000. Total processed: 2000. Time: 0.04s
  Processed batch ending at record 2500. Total processed: 2500. Time: 0.04s
  Processed batch ending at record 3000. Total processed: 3000. Time: 0.04s
  Processed batch ending at record 3500. Total processed: 3500. Time: 0.04s
  Processed batch ending at record 4000. Total processed: 4000. Time: 0.04s
  Processed batch ending at record 4500. Total processed: 4500. Time: 0.05s
  Proce

In [86]:
# %% [markdown]
# ## Step 4: Verify Basic Data Load
#
# This cell checks the `summary_vectors` table to verify that the basic data
# (`doc_id`, `summary`, `file_path`) was loaded correctly in the previous step,
# and that other columns (`embedding`, `cluster_id`, `cluster_name`) remain NULL.

# %%
import sys
import time
import pandas as pd
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
SAMPLE_SIZE = 5 # How many rows to fetch for verification display

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Verify Data ---
session = None
engine = None
df_sample = pd.DataFrame() # Initialize empty DataFrame

print("\nConnecting to database to verify 'summary_vectors' population...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        inspector = sql_inspect(engine)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Check Table Existence and Row Count ---
        print("\n[1/2] Checking table existence and row count...")
        if inspector.has_table("summary_vectors", schema="public"):
            print("   ✅ Table 'public.summary_vectors' exists.")
            count_result = session.execute(
                 text("SELECT COUNT(*) FROM public.summary_vectors;")
             ).scalar_one_or_none()
            row_count = count_result if count_result is not None else 0
            print(f"   📊 Current row count: {row_count}")

            if row_count > 0:
                # --- 2) Fetch Sample and Verify Population ---
                print(f"\n[2/2] Fetching {SAMPLE_SIZE} sample rows for verification...")
                try:
                    # Get current column names to build query dynamically
                    columns_info = inspector.get_columns("summary_vectors", schema="public")
                    existing_columns = [col['name'] for col in columns_info] if columns_info else []

                    if existing_columns:
                        select_cols_str = ", ".join([f'"{col}"' for col in existing_columns])
                        sample_query = text(f"""
                            SELECT {select_cols_str}
                            FROM public.summary_vectors
                            ORDER BY doc_id -- Fetching first few by doc_id
                            LIMIT :limit;
                        """)
                        df_sample = pd.read_sql(sample_query, con=engine, params={'limit': SAMPLE_SIZE})
                        print(f"\n   📄 Sample data ({len(df_sample)} rows):")
                        display(df_sample) # Display DataFrame in notebook

                        # --- Verification Logic ---
                        print("\n   Verification Results (based on sample):")
                        # Columns expected to be populated
                        for col in ['doc_id', 'summary', 'file_path']:
                             if col in df_sample.columns:
                                 is_populated = df_sample[col].notnull().all()
                                 print(f"      - Column '{col}' populated: {is_populated}")
                             else:
                                  print(f"      - Column '{col}' not found.")
                        # Columns expected to be NULL
                        for col in ['embedding', 'cluster_id', 'cluster_name']:
                             if col in df_sample.columns:
                                 is_null = df_sample[col].isnull().all()
                                 print(f"      - Column '{col}' is NULL: {is_null}")
                             else:
                                  print(f"      - Column '{col}' not found.")
                    else:
                        print("      Could not retrieve column names.")

                except Exception as e:
                    print(f"   ⚠️ Error fetching or verifying sample data: {e}")
            else:
                print("   ℹ️ Table is empty. Cannot verify population.")
        else:
             print("   ❌ Table 'public.summary_vectors' does not exist. Cannot verify.")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred: {e}")
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Verification check finished.")

# %% [markdown]
# ## Next Steps
#
# 1. Review the sample data and verification results. Confirm that `doc_id`, `summary`, and `file_path` are populated, and `embedding`, `cluster_id`, `cluster_name` are NULL.
# 2. If correct, proceed to Step 5: Generate and load embeddings.



✅ init_vector_db imported successfully.

Connecting to database to verify 'summary_vectors' population...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.02s

[1/2] Checking table existence and row count...
   ✅ Table 'public.summary_vectors' exists.
   📊 Current row count: 9746

[2/2] Fetching 5 sample rows for verification...

   📄 Sample data (5 rows):


doc_id                                            summary  \
0       3  This document describes the wastewater treatme...   
1       4  This document provides a detailed list of chem...   
2       5  This document is a controlled copy of "0175-SW...   
3       6  This controlled copy of a final clarification ...   
4       7  This document is a controlled copy of a biolog...   

                                           file_path embedding cluster_id  \
0  /data/projects/filefindr/UTILS/TechTeam/8000 W...      None       None   
1  /data/projects/filefindr/UTILS/TechTeam/8000 W...      None       None   
2  /data/projects/filefindr/UTILS/TechTeam/8000 W...      None       None   
3  /data/projects/filefindr/UTILS/TechTeam/8000 W...      None       None   
4  /data/projects/filefindr/UTILS/TechTeam/8000 W...      None       None   

  cluster_name  
0         None  
1         None  
2         None  
3         None  
4         None


   Verification Results (based on sample):
      - Column 'doc_id' populated: True
      - Column 'summary' populated: True
      - Column 'file_path' populated: True
      - Column 'embedding' is NULL: True
      - Column 'cluster_id' is NULL: True
      - Column 'cluster_name' is NULL: True

Database session closed.

✅ Verification check finished.


In [87]:
# %% [markdown]
# ## Step 4.1: View Sample Summaries
#
# This cell fetches and prints a few summaries from the table to give a
# qualitative idea of the content being processed.

# %%
import sys
import time
from sqlalchemy import text
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
SAMPLE_SUMMARY_COUNT = 3 # How many summaries to print

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Fetch Summaries ---
session = None
engine = None

print(f"\nConnecting to database to fetch {SAMPLE_SUMMARY_COUNT} sample summaries...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # Fetch summaries for the first few doc_ids
        query = text("""
            SELECT doc_id, summary
            FROM public.summary_vectors
            WHERE summary IS NOT NULL -- Ensure we get rows with summaries
            ORDER BY doc_id
            LIMIT :limit;
        """)

        results = session.execute(query, {'limit': SAMPLE_SUMMARY_COUNT}).fetchall()

        if results:
            print(f"\n--- Sample Summaries ---")
            for row in results:
                # Use ._mapping to access columns by name easily
                row_dict = row._mapping
                print(f"\n[Doc ID: {row_dict.get('doc_id', 'N/A')}]")
                print(f"{row_dict.get('summary', 'No summary found.')}")
                print("-" * 20) # Separator
        else:
            print("   No summaries found in the table (or table is empty/summary column is NULL).")

    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred while fetching summaries: {e}")
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Summary fetching finished.")

# %% [markdown]
# ## Next Steps
#
# 1. Review the sample summaries.
# 2. Proceed to Step 5: Generate and load embeddings.



✅ init_vector_db imported successfully.

Connecting to database to fetch 3 sample summaries...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

--- Sample Summaries ---

[Doc ID: 3]
This document describes the wastewater treatment plant (WWTP) process, detailing the handling and processing of various types of wastewater streams. Key components include:

- **Booster Pumps**: Maintain minimal header pressure on each system, ensuring consistent discharge of wastewater into common headers.
- **Filter Pots/Strainers**: Remove large solids from wastewater streams before they move through the treatment units.
- **Flow and Pressure Control Systems**: Manage the volume of water sent to hydraulic storage tanks (TK-210).
- **Hydraulic Storage Tanks (TK-210/211)**: Buffer variability in organic and hydraulic loads, with recovery rates controlled based on current process conditions.
- **Vapor Stripping Process (TK-225)**: Removes Volatile Organic Carbon compounds from wastewater stre

In [88]:
# %% [markdown]
# ## Step 5.1: Reset Embeddings to NULL (Optional Cleanup)
#
# Run this cell to set the embedding column back to NULL before regenerating
# them with the correct format.

# %%
import sys
import time
from sqlalchemy import text
import warnings

VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
if VDB_PIPELINE_PATH not in sys.path: sys.path.append(VDB_PIPELINE_PATH)

try: from init_vector_db import init_vector_db; print("✅ init_vector_db imported.")
except ImportError as e: warnings.warn(f"⚠️ Failed import: {e}")

session = None; engine = None
print("\nConnecting to database to reset embeddings...")
try:
    if 'init_vector_db' in globals():
        session, engine = init_vector_db(wipe_database=False)
        print("   Connected.")
        print("   Executing UPDATE to set embeddings to NULL...")
        session.execute(text("UPDATE public.summary_vectors SET embedding = NULL WHERE embedding IS NOT NULL;"))
        session.commit()
        print("   ✅ Embeddings reset to NULL.")
    else: print("   Skipping DB connection.")
except Exception as e: print(f"\n❌ Error resetting embeddings: {e}"); session.rollback()
finally:
    if session: session.close(); print("\nDatabase session closed.")

✅ init_vector_db imported.

Connecting to database to reset embeddings...
CHECKING IF SEARCH INDICES CREATED: True
   Connected.
   Executing UPDATE to set embeddings to NULL...
   ✅ Embeddings reset to NULL.

Database session closed.


In [89]:
# %% [markdown]
# ## Step 5: Generate and Load Embeddings
#
# This cell generates semantic embeddings for the summaries loaded in the previous steps
# and updates the `embedding` column in the `public.summary_vectors` table.
#
# It processes only the rows where the `embedding` is currently `NULL`.

# %%
import sys
import time
import numpy as np
from sqlalchemy import text, bindparam
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
# Specify the Sentence Transformer model to use
# Common choices: 'all-MiniLM-L6-v2', 'multi-qa-MiniLM-L6-cos-v1', 'all-mpnet-base-v2'
# Use the same model as in your original 'load_summaries.py' if possible
MODEL_NAME = 'all-MiniLM-L6-v2' #<-- ADJUST IF NEEDED (Check 'variables.py' from original script?)
BATCH_SIZE = 100 # How many summaries to process and update at a time (adjust based on memory/GPU)

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer and SentenceTransformer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

try:
    from sentence_transformers import SentenceTransformer
    print(f"✅ SentenceTransformer imported successfully.")
except ImportError:
    warnings.warn("⚠️ Failed to import SentenceTransformer. Install it: pip install sentence-transformers")

# --- Load Sentence Transformer Model ---
model = None
if 'SentenceTransformer' in globals():
    print(f"\nLoading Sentence Transformer model: {MODEL_NAME}...")
    model_load_start = time.time()
    try:
        model = SentenceTransformer(MODEL_NAME)
        print(f"   ✅ Model loaded in {time.time() - model_load_start:.2f}s.")
    except Exception as e:
        warnings.warn(f"⚠️ Failed to load model '{MODEL_NAME}': {e}")
else:
    print("Skipping model loading because SentenceTransformer could not be imported.")


# --- Connect to DB and Process Embeddings ---
session = None
engine = None

# Proceed only if model loaded and init_vector_db is available
if model is not None and 'init_vector_db' in globals():
    print("\nConnecting to database to generate and load embeddings...")
    connect_start_time = time.time()
    try:
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- Fetch rows needing embeddings ---
        fetch_start_time = time.time()
        print("\nFetching rows where embedding is NULL...")
        query_select = text("""
            SELECT doc_id, summary
            FROM public.summary_vectors
            WHERE embedding IS NULL AND summary IS NOT NULL;
        """)
        # Fetch all results - adjust if memory becomes an issue for very large tables
        # Consider fetching only IDs then fetching summaries in batches if needed
        rows_to_process = session.execute(query_select).fetchall()
        print(f"   Found {len(rows_to_process)} rows needing embeddings. Fetch time: {time.time() - fetch_start_time:.2f}s")

        if rows_to_process:
            total_processed = 0
            batch_num = 0
            start_time_all_batches = time.time()

            print(f"\nProcessing records in batches of {BATCH_SIZE}...")
            # Prepare the UPDATE statement once
            # Using bindparam() for parameter binding in the update
            query_update = text("""
                UPDATE public.summary_vectors
                SET embedding = :emb
                WHERE doc_id = :doc_id;
            """)

            for i in range(0, len(rows_to_process), BATCH_SIZE):
                batch_num += 1
                batch_start_time = time.time()
                current_batch = rows_to_process[i : i + BATCH_SIZE]
                print(f"  Processing batch {batch_num} ({len(current_batch)} records)...")

                # Extract summaries and corresponding doc_ids for the batch
                summaries_batch = [row._mapping['summary'] for row in current_batch]
                doc_ids_batch = [row._mapping['doc_id'] for row in current_batch]

                # --- Generate Embeddings ---
                # Use model.encode - this can leverage GPU if available
                embeddings_batch = model.encode(summaries_batch, show_progress_bar=False) # Set show_progress_bar=True for visual feedback


                # --- Prepare data for update ---
                update_params = []
                for doc_id, embedding in zip(doc_ids_batch, embeddings_batch):
                    # Explicitly format the embedding list as a string '[num1, num2,...]'
                    # which pgvector typically understands.
                    embedding_str = '[' + ','.join(map(str, embedding.tolist())) + ']'
                    update_params.append({'doc_id': doc_id, 'emb': embedding_str})


                # --- Update Database Batch ---
                try:
                    # Execute update for each item in the batch within one transaction
                    session.execute(query_update, update_params)
                    session.commit() # Commit after each successful batch update
                    total_processed += len(current_batch)
                    print(f"    Batch {batch_num} updated in DB. Total processed: {total_processed}. Time: {time.time() - batch_start_time:.2f}s")
                except Exception as e:
                    warnings.warn(f"⚠️ Error updating batch {batch_num}: {e}")
                    session.rollback() # Rollback the failed batch
                    # Optionally: break or continue processing next batch

            print("\n--------------------")
            print(f"✅ Embedding generation and loading finished.")
            print(f"   Total records processed: {total_processed}")
            print(f"   Total time: {time.time() - start_time_all_batches:.2f}s")
            print("--------------------")

        else:
            print("   No rows found with NULL embeddings. Nothing to process.")

    except Exception as e:
        # Catch errors during connection or the main loop setup
        print(f"\n❌ An error occurred during the embedding process: {e}")
        if session:
            session.rollback()
    finally:
        # --- Close Connection ---
        if session and session.is_active:
            session.close()
            print("\nDatabase session closed.")

elif model is None:
     print("\nSkipping embedding generation because the Sentence Transformer model could not be loaded.")
else:
     print("\nSkipping embedding generation because init_vector_db could not be imported.")


# %% [markdown]
# ## Next Steps
#
# 1. The `embedding` column in `summary_vectors` should now be populated for all rows that previously had `NULL`.
# 2. You can run a verification cell next to confirm this.
# 3. The next logical step after verification is clustering the documents based on these embeddings.



✅ init_vector_db imported successfully.
✅ SentenceTransformer imported successfully.

Loading Sentence Transformer model: all-MiniLM-L6-v2...
   ✅ Model loaded in 0.91s.

Connecting to database to generate and load embeddings...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

Fetching rows where embedding is NULL...
   Found 9746 rows needing embeddings. Fetch time: 0.03s

Processing records in batches of 100...
  Processing batch 1 (100 records)...
    Batch 1 updated in DB. Total processed: 100. Time: 0.07s
  Processing batch 2 (100 records)...
    Batch 2 updated in DB. Total processed: 200. Time: 0.07s
  Processing batch 3 (100 records)...
    Batch 3 updated in DB. Total processed: 300. Time: 0.07s
  Processing batch 4 (100 records)...
    Batch 4 updated in DB. Total processed: 400. Time: 0.07s
  Processing batch 5 (100 records)...
    Batch 5 updated in DB. Total processed: 500. Time: 0.06s
  Processing batch 6 (100 records)...
    Batch 6 updated in DB. Total pr

    Batch 10 updated in DB. Total processed: 1000. Time: 0.07s
  Processing batch 11 (100 records)...
    Batch 11 updated in DB. Total processed: 1100. Time: 0.08s
  Processing batch 12 (100 records)...
    Batch 12 updated in DB. Total processed: 1200. Time: 0.07s
  Processing batch 13 (100 records)...
    Batch 13 updated in DB. Total processed: 1300. Time: 0.07s
  Processing batch 14 (100 records)...
    Batch 14 updated in DB. Total processed: 1400. Time: 0.07s
  Processing batch 15 (100 records)...
    Batch 15 updated in DB. Total processed: 1500. Time: 0.07s
  Processing batch 16 (100 records)...
    Batch 16 updated in DB. Total processed: 1600. Time: 0.07s
  Processing batch 17 (100 records)...
    Batch 17 updated in DB. Total processed: 1700. Time: 0.07s
  Processing batch 18 (100 records)...
    Batch 18 updated in DB. Total processed: 1800. Time: 0.07s
  Processing batch 19 (100 records)...
    Batch 19 updated in DB. Total processed: 1900. Time: 0.07s
  Processing batch 

In [90]:
# %% [markdown]
# ## Step 6: Verify Embedding Population (Handling String Readback)
#
# This cell checks the `summary_vectors` table to verify that the `embedding`
# column was populated. It includes logic to handle cases where the embedding
# might be read back as a string and attempts to parse it to check the dimension.

# %%
import sys
import time
import pandas as pd
import numpy as np
import ast # For safely evaluating string representations of lists
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
SAMPLE_SIZE = 2 # How many rows to fetch for verification display
EXPECTED_DIMENSION = 384 # The dimension embeddings should have

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Verify Data ---
session = None
engine = None
df_sample = pd.DataFrame() # Initialize empty DataFrame

print("\nConnecting to database to verify 'summary_vectors' embedding population...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check if import succeeded
        session, engine = init_vector_db(wipe_database=False)
        inspector = sql_inspect(engine)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Check Table Existence and Row Count ---
        print("\n[1/2] Checking table existence and row count...")
        if inspector.has_table("summary_vectors", schema="public"):
            print("   ✅ Table 'public.summary_vectors' exists.")
            count_result = session.execute(
                 text("SELECT COUNT(*) FROM public.summary_vectors;")
             ).scalar_one_or_none()
            row_count = count_result if count_result is not None else 0
            print(f"   📊 Current row count: {row_count}")

            # Check count of non-NULL embeddings
            count_non_null_emb = session.execute(
                text("SELECT COUNT(*) FROM public.summary_vectors WHERE embedding IS NOT NULL;")
            ).scalar_one_or_none()
            print(f"   📊 Rows with non-NULL embeddings: {count_non_null_emb or 0}")


            if row_count > 0 and (count_non_null_emb or 0) > 0:
                # --- 2) Fetch Sample and Verify Embeddings ---
                print(f"\n[2/2] Fetching {SAMPLE_SIZE} sample rows for embedding verification...")
                try:
                    # Get current column names to build query dynamically
                    columns_info = inspector.get_columns("summary_vectors", schema="public")
                    existing_columns = [col['name'] for col in columns_info] if columns_info else []

                    if 'embedding' not in existing_columns:
                         print("   ❌ Embedding column not found in table. Cannot verify.")
                    elif existing_columns:
                        select_cols_str = ", ".join([f'"{col}"' for col in existing_columns])
                        sample_query = text(f"""
                            SELECT {select_cols_str}
                            FROM public.summary_vectors
                            WHERE embedding IS NOT NULL -- Fetch rows that *should* have embeddings
                            ORDER BY doc_id
                            LIMIT :limit;
                        """)
                        df_sample = pd.read_sql(sample_query, con=engine, params={'limit': SAMPLE_SIZE})

                        if not df_sample.empty:
                            print(f"\n   📄 Sample data with non-NULL embeddings ({len(df_sample)} rows):")
                            # Display relevant columns only for clarity
                            display_cols = ['doc_id', 'summary', 'embedding']
                            display(df_sample[[col for col in display_cols if col in df_sample.columns]])

                            # --- Verification Logic ---
                            print("\n   Verification Results (based on sample):")
                            # Check if 'embedding' column has non-NULL values in the sample
                            embeddings_populated = df_sample['embedding'].notnull().all()
                            print(f"      - Embedding column populated in sample: {embeddings_populated}")

                            # Check the type and dimension of the first embedding in the sample
                            if embeddings_populated:
                                first_embedding_raw = df_sample['embedding'].iloc[0]
                                emb_type_raw = type(first_embedding_raw).__name__
                                print(f"      - Raw type of first embedding: {emb_type_raw}")

                                parsed_embedding = None
                                # --- Attempt to parse if it's a string ---
                                if isinstance(first_embedding_raw, str):
                                    print("      - Attempting to parse string embedding...")
                                    try:
                                        # Use ast.literal_eval for safe evaluation of string lists/tuples etc.
                                        # Assumes format like '[1.0, 2.0, ...]'
                                        parsed_embedding = ast.literal_eval(first_embedding_raw)
                                        print("        ✅ Parsed successfully.")
                                    except (ValueError, SyntaxError) as parse_error:
                                        print(f"        ❌ Failed to parse string: {parse_error}")
                                elif isinstance(first_embedding_raw, (list, np.ndarray)):
                                     # If it's already a list or array, use it directly
                                     parsed_embedding = first_embedding_raw
                                else:
                                     print(f"      - Cannot determine length of embedding (type: {emb_type_raw}).")


                                # --- Check length of parsed embedding ---
                                if parsed_embedding is not None and isinstance(parsed_embedding, (list, np.ndarray)):
                                    emb_len = len(parsed_embedding)
                                    print(f"      - Length of PARSED first embedding: {emb_len}")
                                    if emb_len == EXPECTED_DIMENSION:
                                        print(f"        ✅ Matches expected dimension ({EXPECTED_DIMENSION}).")
                                    else:
                                        print(f"        ❌ Does NOT match expected dimension ({EXPECTED_DIMENSION}).")
                                elif parsed_embedding is not None:
                                     print(f"      - Parsed embedding is not a list/array (type: {type(parsed_embedding).__name__}). Cannot check length.")


                        else:
                             print("   ℹ️ Could not fetch sample rows with non-NULL embeddings.")
                    else:
                        print("      Could not retrieve column names.")

                except Exception as e:
                    print(f"   ⚠️ Error fetching or verifying sample data: {e}")
            elif row_count > 0:
                 print("   ℹ️ Table has rows, but no non-NULL embeddings found.")
            else:
                print("   ℹ️ Table is empty. Cannot verify population.")
        else:
             print("   ❌ Table 'public.summary_vectors' does not exist. Cannot verify.")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred: {e}")
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Verification check finished.")

# %% [markdown]
# ## Next Steps
#
# 1. Review the verification results. Hopefully, it now shows that the *parsed* embedding length matches the expected dimension (384).
# 2. If the parsing fails or the length is still wrong, there might be an issue with the format of the string being stored in the database.
# 3. If it verifies correctly, proceed to Step 7: Clustering.



✅ init_vector_db imported successfully.

Connecting to database to verify 'summary_vectors' embedding population...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.02s

[1/2] Checking table existence and row count...
   ✅ Table 'public.summary_vectors' exists.
   📊 Current row count: 9746
   📊 Rows with non-NULL embeddings: 9746

[2/2] Fetching 2 sample rows for embedding verification...

   📄 Sample data with non-NULL embeddings (2 rows):


doc_id                                            summary  \
0       3  This document describes the wastewater treatme...   
1       4  This document provides a detailed list of chem...   

                                           embedding  
0  [-0.063856415,0.047084585,0.015344447,-0.07125...  
1  [-0.015133503,-0.044503696,-0.05541039,-0.0645...


   Verification Results (based on sample):
      - Embedding column populated in sample: True
      - Raw type of first embedding: str
      - Attempting to parse string embedding...
        ✅ Parsed successfully.
      - Length of PARSED first embedding: 384
        ✅ Matches expected dimension (384).

Database session closed.

✅ Verification check finished.


In [91]:
# %% [markdown]
# ## Step 7: Perform Clustering Test (In Memory)
#
# This cell fetches the populated embeddings, runs KMeans clustering on them
# in memory, and analyzes the results (e.g., cluster sizes) without
# updating the database. This allows evaluating the clustering before committing.

# %%
import sys
import time
import pandas as pd
import numpy as np
import ast # For safely evaluating string representations of lists
from sqlalchemy import text, inspect as sql_inspect
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score # Uncomment to calculate silhouette score
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
EXPECTED_DIMENSION = 384 # Should match the embedding dimension
N_CLUSTERS = 10 # How many clusters to find (you can experiment with this)
RANDOM_STATE = 42 # For reproducible clustering results

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Import Scikit-learn ---
try:
    from sklearn.cluster import KMeans
    # from sklearn.metrics import silhouette_score # Uncomment for silhouette score
    print("✅ Scikit-learn imported successfully.")
except ImportError:
     warnings.warn("⚠️ Failed to import scikit-learn. Install it: pip install scikit-learn")


# --- Connect, Fetch, Parse, and Cluster ---
session = None
engine = None
embedding_matrix = None # To hold the numerical embeddings
doc_ids = [] # To keep track of doc_ids corresponding to rows in embedding_matrix

print("\nConnecting to database to fetch embeddings for clustering test...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals() and 'KMeans' in globals(): # Check imports
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Fetch Embeddings ---
        fetch_start_time = time.time()
        print("\n[1/3] Fetching non-NULL embeddings...")
        query_select = text("""
            SELECT doc_id, embedding
            FROM public.summary_vectors
            WHERE embedding IS NOT NULL;
        """)
        # Fetch all results. Consider batching if memory is an issue.
        results = session.execute(query_select).fetchall()
        print(f"   Fetched {len(results)} embeddings in {time.time() - fetch_start_time:.2f}s")

        if results:
            # --- 2) Parse Embeddings ---
            parse_start_time = time.time()
            print("\n[2/3] Parsing embeddings (expecting string format)...")
            parsed_embeddings_list = []
            valid_rows = 0
            skipped_rows = 0
            for row in results:
                doc_id = row._mapping['doc_id']
                embedding_raw = row._mapping['embedding']
                parsed_embedding = None
                if isinstance(embedding_raw, str):
                    try:
                        # Use ast.literal_eval for safe evaluation
                        parsed_embedding = ast.literal_eval(embedding_raw)
                        if isinstance(parsed_embedding, list) and len(parsed_embedding) == EXPECTED_DIMENSION:
                             parsed_embeddings_list.append(parsed_embedding)
                             doc_ids.append(doc_id) # Keep track of the doc_id for this valid embedding
                             valid_rows += 1
                        else:
                             warnings.warn(f"Skipping doc_id {doc_id}: Parsed embedding is not a list or has wrong dimension ({len(parsed_embedding) if isinstance(parsed_embedding, list) else 'N/A'}).")
                             skipped_rows += 1
                    except (ValueError, SyntaxError) as parse_error:
                        warnings.warn(f"Skipping doc_id {doc_id}: Failed to parse embedding string: {parse_error}")
                        skipped_rows += 1
                # Optional: Handle case where embedding is already list/array (shouldn't happen based on previous step)
                # elif isinstance(embedding_raw, (list, np.ndarray)) and len(embedding_raw) == EXPECTED_DIMENSION:
                #    parsed_embeddings_list.append(list(embedding_raw)) # Ensure it's a list
                #    doc_ids.append(doc_id)
                #    valid_rows += 1
                else:
                    warnings.warn(f"Skipping doc_id {doc_id}: Embedding is not a string or could not be processed (type: {type(embedding_raw).__name__}).")
                    skipped_rows += 1

            if not parsed_embeddings_list:
                 raise ValueError("No valid embeddings could be parsed. Cannot proceed with clustering.")

            # Convert the list of lists into a NumPy matrix for scikit-learn
            embedding_matrix = np.array(parsed_embeddings_list)
            print(f"   Parsed {valid_rows} valid embeddings into matrix shape: {embedding_matrix.shape}. Skipped: {skipped_rows}.")
            print(f"   Parsing finished in {time.time() - parse_start_time:.2f}s")

            # --- 3) Perform KMeans Clustering ---
            cluster_start_time = time.time()
            print(f"\n[3/3] Performing KMeans clustering (k={N_CLUSTERS})...")
            kmeans = KMeans(n_clusters=N_CLUSTERS, random_state=RANDOM_STATE, n_init=10) # n_init=10 is default and recommended
            cluster_assignments = kmeans.fit_predict(embedding_matrix)
            print(f"   KMeans finished in {time.time() - cluster_start_time:.2f}s")

            # --- Analyze Results ---
            print("\n--- Clustering Test Results ---")
            # Create a temporary DataFrame for analysis
            df_results = pd.DataFrame({'doc_id': doc_ids, 'cluster_id': cluster_assignments})

            # Calculate and print cluster sizes
            cluster_counts = df_results['cluster_id'].value_counts().sort_index()
            print("\nCluster Sizes (Distribution):")
            print(cluster_counts)

            # --- Optional: Calculate Silhouette Score ---
            # Silhouette score measures how similar an object is to its own cluster
            # compared to other clusters. Ranges from -1 to 1. Higher is better.
            # Can be computationally expensive for large datasets.
            if 'silhouette_score' in globals():
                print("\nCalculating Silhouette Score (may take time)...")
                silhouette_start_time = time.time()
                # Reduce sample size for faster calculation if needed
                sample_indices = np.random.choice(embedding_matrix.shape[0], size=min(5000, embedding_matrix.shape[0]), replace=False)
                score = silhouette_score(embedding_matrix[sample_indices], cluster_assignments[sample_indices], metric='cosine')
                score = silhouette_score(embedding_matrix, cluster_assignments, metric='cosine') # Use 'cosine' for high-dim text data
                print(f"   Silhouette Score: {score:.4f}")
                print(f"   Calculation time: {time.time() - silhouette_start_time:.2f}s")
            else:
                print("\nSilhouette score calculation skipped (sklearn.metrics not imported or calculation commented out).")


            # --- Optional: Show sample summaries per cluster ---
            # This requires fetching summaries again, could be slow.
            print("\n--- Sample Summaries per Cluster (Example) ---")
            try:
               # Fetch summaries for the doc_ids we clustered
               summary_query = text("SELECT doc_id, summary FROM public.summary_vectors WHERE doc_id = ANY(:doc_ids)")
               summary_results = session.execute(summary_query, {'doc_ids': doc_ids}).fetchall()
               summary_map = {row._mapping['doc_id']: row._mapping['summary'] for row in summary_results}
               df_results['summary'] = df_results['doc_id'].map(summary_map)
            
               for cluster_num in sorted(df_results['cluster_id'].unique()):
                   print(f"\n--- Cluster {cluster_num} Samples ---")
                   cluster_sample = df_results[df_results['cluster_id'] == cluster_num].head(3) # Show first 3
                   for _, row in cluster_sample.iterrows():
                        print(f"  [Doc ID: {row['doc_id']}] {row['summary'][:200]}...") # Print summary preview
            except Exception as e:
                print(f"  ⚠️ Could not fetch or display sample summaries: {e}")


        else:
            print("   No embeddings found in the table. Cannot perform clustering.")

    else:
        print("   Skipping clustering test because dependencies are missing (init_vector_db or scikit-learn).")

except Exception as e:
    print(f"\n❌ An unexpected error occurred during the clustering test: {e}")
    if session:
        session.rollback() # Just in case, though no commits should happen here
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Clustering test finished.")

# %% [markdown]
# ## Next Steps
#
# 1. Review the cluster size distribution. Are the clusters reasonably balanced, or is there one giant cluster and many tiny ones?
# 2. (If enabled) Evaluate the Silhouette Score. Scores closer to 1 are better. Scores near 0 or negative indicate overlapping clusters.
# 3. Based on the results, you might want to:
#     - Adjust `N_CLUSTERS` and re-run this cell.
#     - Try a different clustering algorithm (e.g., Hierarchical).
#     - Proceed to Step 8: Update the database with these cluster assignments if satisfied.



✅ init_vector_db imported successfully.
✅ Scikit-learn imported successfully.

Connecting to database to fetch embeddings for clustering test...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

[1/3] Fetching non-NULL embeddings...


   Fetched 9746 embeddings in 0.16s

[2/3] Parsing embeddings (expecting string format)...
   Parsed 9746 valid embeddings into matrix shape: (9746, 384). Skipped: 0.
   Parsing finished in 4.27s

[3/3] Performing KMeans clustering (k=10)...
   KMeans finished in 1.15s

--- Clustering Test Results ---

Cluster Sizes (Distribution):
cluster_id
0    1465
1     982
2     601
3     907
4    1035
5    1197
6     815
7     900
8     877
9     967
Name: count, dtype: int64

Calculating Silhouette Score (may take time)...
   Silhouette Score: 0.0887
   Calculation time: 0.54s

--- Sample Summaries per Cluster (Example) ---

--- Cluster 0 Samples ---
  [Doc ID: 417] This document specifies the NO. 375 SERIES 71 COUPLING, detailing its components like coupling hubs, disc packs, bolts, washers, and center members. It provides part numbers, descriptions, quantities,...
  [Doc ID: 817] This document provides detailed technical drawings and specifications for a Series 1000 Simplicity Metering Pump, 

In [92]:
# %% [markdown]
# ## Step 8: Update Database with Cluster Assignments
#
# This cell takes the cluster assignments calculated in the previous step (Step 7)
# and updates the `cluster_id` column in the `public.summary_vectors` table.
#
# **Note:** This cell relies on the `df_results` DataFrame (containing `doc_id`
# and `cluster_id`) being available in memory from running Step 7 immediately prior.
# It leaves the `cluster_name` column as NULL.

# %%
import sys
import time
import pandas as pd
from sqlalchemy import text, bindparam
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
BATCH_SIZE = 500 # How many rows to update in each database transaction

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Check if results from Step 7 are available ---
if 'df_results' not in locals() or not isinstance(df_results, pd.DataFrame) or 'doc_id' not in df_results.columns or 'cluster_id' not in df_results.columns:
    warnings.warn("⚠️ Clustering results ('df_results' DataFrame with 'doc_id' and 'cluster_id') not found in memory. Please run Step 7 (Clustering Test) immediately before this cell.")
    # Optionally stop execution:
    # raise NameError("Clustering results not found. Run Step 7 first.")
    can_proceed = False
else:
    print(f"✅ Found clustering results for {len(df_results)} documents from Step 7.")
    can_proceed = True

# --- Connect to DB and Update Cluster IDs ---
session = None
engine = None

# Proceed only if results are available and init_vector_db is imported
if can_proceed and 'init_vector_db' in globals():
    print("\nConnecting to database to update cluster IDs...")
    connect_start_time = time.time()
    try:
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        total_updated = 0
        batch_num = 0
        start_time_all_batches = time.time()

        print(f"\nUpdating cluster IDs in batches of {BATCH_SIZE}...")
        # Prepare the UPDATE statement once
        query_update = text("""
            UPDATE public.summary_vectors
            SET cluster_id = :cluster_id
            WHERE doc_id = :doc_id;
        """)

        # Convert DataFrame rows to list of dictionaries for execute
        update_data = df_results[['doc_id', 'cluster_id']].to_dict('records')

        for i in range(0, len(update_data), BATCH_SIZE):
            batch_num += 1
            batch_start_time = time.time()
            current_batch_params = update_data[i : i + BATCH_SIZE]
            print(f"  Processing update batch {batch_num} ({len(current_batch_params)} records)...")

            # --- Update Database Batch ---
            try:
                # Execute update for the entire batch within one transaction
                session.execute(query_update, current_batch_params)
                session.commit() # Commit after each successful batch update
                total_updated += len(current_batch_params)
                print(f"    Batch {batch_num} committed. Total updated: {total_updated}. Time: {time.time() - batch_start_time:.2f}s")
            except Exception as e:
                warnings.warn(f"⚠️ Error updating batch {batch_num}: {e}")
                session.rollback() # Rollback the failed batch
                # Optionally: break or continue processing next batch

        print("\n--------------------")
        print(f"✅ Cluster ID update finished.")
        print(f"   Total records updated: {total_updated}")
        print(f"   Total time: {time.time() - start_time_all_batches:.2f}s")
        print("--------------------")


    except Exception as e:
        # Catch errors during connection or the main loop setup
        print(f"\n❌ An error occurred during the database update process: {e}")
        if session:
            session.rollback()
    finally:
        # --- Close Connection ---
        if session and session.is_active:
            session.close()
            print("\nDatabase session closed.")

elif not can_proceed:
     print("\nSkipping database update because previous clustering results were not found.")
else:
     print("\nSkipping database update because init_vector_db could not be imported.")


# %% [markdown]
# ## Next Steps
#
# 1. The `cluster_id` column in `summary_vectors` should now be populated based on the clustering results from Step 7.
# 2. You can run a verification cell or query the database directly to confirm.
# 3. Now, proceed to Step 9: Visualize the clusters.



✅ init_vector_db imported successfully.
✅ Found clustering results for 9746 documents from Step 7.

Connecting to database to update cluster IDs...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

Updating cluster IDs in batches of 500...
  Processing update batch 1 (500 records)...
    Batch 1 committed. Total updated: 500. Time: 0.05s
  Processing update batch 2 (500 records)...
    Batch 2 committed. Total updated: 1000. Time: 0.05s
  Processing update batch 3 (500 records)...
    Batch 3 committed. Total updated: 1500. Time: 0.05s
  Processing update batch 4 (500 records)...
    Batch 4 committed. Total updated: 2000. Time: 0.05s
  Processing update batch 5 (500 records)...
    Batch 5 committed. Total updated: 2500. Time: 0.05s
  Processing update batch 6 (500 records)...
    Batch 6 committed. Total updated: 3000. Time: 0.05s
  Processing update batch 7 (500 records)...
    Batch 7 committed. Total updated: 3500. Time: 0.05s
  Processing update batch 8 (500 records

In [93]:
# %% [markdown]
# ## Step 9: Visualize Clusters using t-SNE
#
# This cell fetches the embeddings and their assigned cluster IDs from the database,
# performs t-SNE dimensionality reduction on the embeddings (reducing them to 2D),
# and creates an interactive scatter plot to visualize the clusters.

# %%
import sys
import time
import pandas as pd
import numpy as np
import ast # For safely evaluating string representations of lists
from sqlalchemy import text, inspect as sql_inspect
from sklearn.manifold import TSNE # For t-SNE dimensionality reduction
import plotly.express as px
import plotly.io as pio
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
EXPECTED_DIMENSION = 384 # Should match the embedding dimension
RANDOM_STATE = 42 # For reproducible t-SNE results
# t-SNE Parameters (can be tuned)
TSNE_PERPLEXITY = 30  # Typical value, relates to local neighborhood size
TSNE_ITERATIONS = 300 # Number of optimization iterations (increase for potentially better layout, but slower)
TSNE_COMPONENTS = 2   # Reduce to 2 dimensions for plotting

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Import Scikit-learn and Plotly ---
try:
    from sklearn.manifold import TSNE
    print("✅ Scikit-learn (TSNE) imported successfully.")
except ImportError:
     warnings.warn("⚠️ Failed to import scikit-learn. Install it: pip install scikit-learn")

try:
    import plotly.express as px
    import plotly.io as pio
    # Set default renderer for notebooks (or use 'browser', 'vscode', etc.)
    pio.renderers.default = "plotly_mimetype+notebook_connected"
    print("✅ Plotly imported successfully.")
except ImportError:
     warnings.warn("⚠️ Failed to import Plotly. Install it: pip install plotly")


# --- Connect, Fetch, Parse, Reduce Dimensions, and Plot ---
session = None
engine = None
embedding_matrix = None # To hold the numerical embeddings
df_plot = pd.DataFrame() # To hold data for plotting

print("\nConnecting to database to fetch data for visualization...")
connect_start_time = time.time()

try:
    # Check if necessary libraries are available
    if 'init_vector_db' in globals() and 'TSNE' in globals() and 'px' in globals():
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Fetch Embeddings, Cluster IDs, and Summaries ---
        fetch_start_time = time.time()
        print("\n[1/4] Fetching embeddings, cluster IDs, and summaries...")
        # Fetch all necessary columns
        query_select = text("""
            SELECT doc_id, embedding, cluster_id, summary
            FROM public.summary_vectors
            WHERE embedding IS NOT NULL AND cluster_id IS NOT NULL;
        """)
        # Fetch all results into a DataFrame
        df_plot = pd.read_sql(query_select, con=engine)
        print(f"   Fetched {len(df_plot)} records in {time.time() - fetch_start_time:.2f}s")

        if not df_plot.empty:
            # --- 2) Parse Embeddings ---
            parse_start_time = time.time()
            print("\n[2/4] Parsing embeddings...")
            parsed_embeddings_list = []
            valid_indices = [] # Keep track of indices of valid rows in df_plot
            skipped_rows = 0

            for index, embedding_raw in df_plot['embedding'].items():
                parsed_embedding = None
                if isinstance(embedding_raw, str):
                    try:
                        parsed_embedding = ast.literal_eval(embedding_raw)
                        if isinstance(parsed_embedding, list) and len(parsed_embedding) == EXPECTED_DIMENSION:
                             parsed_embeddings_list.append(parsed_embedding)
                             valid_indices.append(index) # Store original DataFrame index
                        else:
                             skipped_rows += 1
                    except (ValueError, SyntaxError):
                        skipped_rows += 1
                # Optional: Handle case if already list/array
                # elif isinstance(embedding_raw, (list, np.ndarray)) and len(embedding_raw) == EXPECTED_DIMENSION:
                #    parsed_embeddings_list.append(list(embedding_raw))
                #    valid_indices.append(index)
                else:
                    skipped_rows += 1

            if skipped_rows > 0:
                 warnings.warn(f"Skipped {skipped_rows} rows during embedding parsing.")

            if not parsed_embeddings_list:
                 raise ValueError("No valid embeddings could be parsed. Cannot proceed with visualization.")

            # Filter the DataFrame to only include rows with valid embeddings
            df_plot = df_plot.loc[valid_indices].copy()
            # Convert the list of lists into a NumPy matrix
            embedding_matrix = np.array(parsed_embeddings_list)
            print(f"   Parsed {len(df_plot)} valid embeddings into matrix shape: {embedding_matrix.shape}.")
            print(f"   Parsing finished in {time.time() - parse_start_time:.2f}s")

            # --- 3) Perform t-SNE Dimensionality Reduction ---
            tsne_start_time = time.time()
            print(f"\n[3/4] Performing t-SNE reduction ({embedding_matrix.shape[1]}D -> {TSNE_COMPONENTS}D)...")
            print(f"   (perplexity={TSNE_PERPLEXITY}, iterations={TSNE_ITERATIONS}) - This may take a while...")

            tsne = TSNE(n_components=TSNE_COMPONENTS,
                        perplexity=TSNE_PERPLEXITY,
                        n_iter=TSNE_ITERATIONS,
                        random_state=RANDOM_STATE,
                        metric='cosine', # Cosine distance often works well for high-dim text embeddings
                        n_jobs=-1) # Use all available CPU cores

            tsne_results = tsne.fit_transform(embedding_matrix)

            # Add t-SNE results to the DataFrame
            df_plot['tsne_1'] = tsne_results[:, 0]
            df_plot['tsne_2'] = tsne_results[:, 1]
            if TSNE_COMPONENTS == 3:
                df_plot['tsne_3'] = tsne_results[:, 2]

            print(f"   t-SNE finished in {time.time() - tsne_start_time:.2f}s")

            # --- 4) Create Interactive Plot ---
            plot_start_time = time.time()
            print("\n[4/4] Generating interactive plot...")

            # Create a summary preview for hover
            df_plot['summary_preview'] = df_plot['summary'].str[:150] + '...'
            # Ensure cluster_id is treated as a category for coloring
            df_plot['cluster_id'] = df_plot['cluster_id'].astype('category')

            plot_params = {
                'data_frame': df_plot,
                'x': 'tsne_1',
                'y': 'tsne_2',
                'color': 'cluster_id', # Color points by cluster ID
                'hover_data': ['doc_id', 'summary_preview', 'cluster_id'],
                'title': f'Document Clusters Visualization (t-SNE, k={df_plot["cluster_id"].nunique()})',
                'labels': {'tsne_1': 't-SNE Dimension 1', 'tsne_2': 't-SNE Dimension 2'},
                'category_orders': {"cluster_id": sorted(df_plot['cluster_id'].unique())} # Consistent legend order
            }

            if TSNE_COMPONENTS == 3:
                plot_params['z'] = 'tsne_3'
                plot_params['labels']['tsne_3'] = 't-SNE Dimension 3'
                fig = px.scatter_3d(**plot_params)
            else:
                fig = px.scatter(**plot_params)

            # Improve layout and marker appearance
            fig.update_traces(marker=dict(size=5, opacity=0.7))
            fig.update_layout(margin=dict(l=0, r=0, b=0, t=40), legend_title_text='Cluster ID')

            # Display the plot
            fig.show()
            print(f"   Plotting finished in {time.time() - plot_start_time:.2f}s")


        else:
            print("   No records found with embeddings and cluster IDs. Cannot visualize.")

    else:
        print("   Skipping visualization because dependencies are missing.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred during the visualization process: {e}")
    if session:
        session.rollback()
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Visualization attempt finished.")

# %% [markdown]
# ## Next Steps
#
# 1. Analyze the interactive plot. Do the clusters appear visually separated? Does the 2D representation align with the themes observed in the sample summaries?
# 2. Hover over points to explore individual documents and their summaries within the clusters.
# 3. Based on this visualization, you might decide to:
#     - Refine clustering parameters (like `k`) and repeat Steps 7-9.
#     - Proceed with using these clusters for downstream tasks.
#     - Manually assign descriptive names to the clusters (Step 10).



✅ init_vector_db imported successfully.
✅ Scikit-learn (TSNE) imported successfully.
✅ Plotly imported successfully.

Connecting to database to fetch data for visualization...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

[1/4] Fetching embeddings, cluster IDs, and summaries...


   Fetched 9746 records in 0.18s

[2/4] Parsing embeddings...
   Parsed 9746 valid embeddings into matrix shape: (9746, 384).
   Parsing finished in 3.98s

[3/4] Performing t-SNE reduction (384D -> 2D)...
   (perplexity=30, iterations=300) - This may take a while...


/home/jonathan_morse/miniconda3/envs/ragui_env/lib/python3.13/site-packages/sklearn/manifold/_t_sne.py:1164: FutureWarning:

'n_iter' was renamed to 'max_iter' in version 1.5 and will be removed in 1.7.



   t-SNE finished in 5.63s

[4/4] Generating interactive plot...


   Plotting finished in 0.10s

Database session closed.

✅ Visualization attempt finished.


In [94]:
# %% [markdown]
# ## Step 10: Fetch Samples for Manual Cluster Naming
#
# This cell fetches sample records (doc_id, summary, file_path) for each
# cluster ID (0-9) to help in manually determining descriptive names for each cluster.

# %%
import sys
import time
import pandas as pd
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
N_CLUSTERS = 10 # Should match the number of clusters used in Step 7
SAMPLES_PER_CLUSTER = 15 # How many samples to fetch for each cluster review
SUMMARY_PREVIEW_LENGTH = 250 # Max characters for summary preview

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Fetch Samples ---
session = None
engine = None

print("\nConnecting to database to fetch samples for each cluster...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check import succeeded
        session, engine = init_vector_db(wipe_database=False)
        inspector = sql_inspect(engine)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- Check if table and necessary columns exist ---
        print("\nChecking table structure...")
        if inspector.has_table("summary_vectors", schema="public"):
            columns_info = inspector.get_columns("summary_vectors", schema="public")
            existing_columns = [col['name'] for col in columns_info] if columns_info else []
            required_cols = ['doc_id', 'summary', 'file_path', 'cluster_id']
            if all(col in existing_columns for col in required_cols):
                print("   ✅ Table and required columns exist.")

                # --- Loop through each cluster ID and fetch samples ---
                print(f"\nFetching {SAMPLES_PER_CLUSTER} samples for each of the {N_CLUSTERS} clusters...")
                fetch_start_time = time.time()

                for cluster_id_to_fetch in range(N_CLUSTERS):
                    print(f"\n{'='*15} Cluster ID: {cluster_id_to_fetch} {'='*15}")
                    query = text("""
                        SELECT doc_id, summary, file_path
                        FROM public.summary_vectors
                        WHERE cluster_id = :cluster_id
                          AND summary IS NOT NULL
                        ORDER BY doc_id -- Or any other order desired
                        LIMIT :limit;
                    """)
                    results = session.execute(query, {
                        'cluster_id': cluster_id_to_fetch,
                        'limit': SAMPLES_PER_CLUSTER
                    }).fetchall()

                    if results:
                        for i, row in enumerate(results):
                            row_dict = row._mapping
                            summary_preview = row_dict.get('summary', '')[:SUMMARY_PREVIEW_LENGTH]
                            if len(row_dict.get('summary', '')) > SUMMARY_PREVIEW_LENGTH:
                                summary_preview += "..."
                            print(f"\n  Sample {i+1}:")
                            print(f"    Doc ID:    {row_dict.get('doc_id', 'N/A')}")
                            print(f"    File Path: {row_dict.get('file_path', 'N/A')}")
                            print(f"    Summary:   {summary_preview}")
                        print(f"{'='*42}") # End marker for the cluster
                    else:
                        print(f"   No samples found for cluster ID {cluster_id_to_fetch}.")

                print(f"\nSample fetching finished in {time.time() - fetch_start_time:.2f}s")

            else:
                missing_cols = [col for col in required_cols if col not in existing_columns]
                print(f"   ❌ Required columns missing: {', '.join(missing_cols)}. Cannot fetch samples.")
        else:
             print("   ❌ Table 'public.summary_vectors' does not exist.")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred: {e}")
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Sample fetching for manual review finished.")

# %% [markdown]
# ## Next Steps
#
# 1. **Review the output above:** Carefully read the summaries and file paths for each cluster ID (0-9).
# 2. **Identify Themes:** Look for common topics, document types, keywords, or purposes within each cluster.
# 3. **Assign Names:** Based on the themes, decide on a concise, descriptive name for each cluster ID. Keep track of these names (e.g., in a separate text file or markdown cell).
#     *Example:*
#     * Cluster 0: Forms / Checklists
#     * Cluster 1: Safety / Process Systems
#     * Cluster 2: Technical Specs / Drawings
#     * ... etc. ...
# 4. **Proceed to Step 11:** Create a cell to update the `cluster_name` column in the database using the names you just decided on.



✅ init_vector_db imported successfully.

Connecting to database to fetch samples for each cluster...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.02s

Checking table structure...
   ✅ Table and required columns exist.

Fetching 15 samples for each of the 10 clusters...

=============== Cluster ID: 0 ===============

  Sample 1:
    Doc ID:    10
    File Path: /data/projects/filefindr/UTILS/TechTeam/8000 WWTP/Equipment/Inlet Cooler Calcs/2017-10-18 Email  MEG to JFDP 02.pdf
    Summary:   This document discusses the procurement of new heat exchangers for BASF Corporation's cooling system in Geismar, Louisiana. It focuses on obtaining a quote from GEO Heat Exchangers, LLC for designing and fabricating heat exchangers capable of handlin...

  Sample 2:
    Doc ID:    19
    File Path: /data/projects/filefindr/UTILS/TechTeam/8000 WWTP/WWTP Constr Books/WWTP Expansion Mech II Pkg for Contract Award Bk 1/20120215190221_001.PDF
    Summary:   This document specifies detailed de

In [95]:
# %% [markdown]
# ## Step 11: Update Database with Cluster Names
#
# This cell updates the `cluster_name` column in the `public.summary_vectors` table
# based on the descriptive names determined in the previous step (manual review or LLM suggestion).

# %%
import sys
import time
from sqlalchemy import text, bindparam
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED

# --- Cluster Name Mapping ---
# Define the names for each cluster ID based on your review/LLM output
# !! Verify these names are exactly what you want !!
cluster_id_to_name = {
    0: "Plant Utilities & Equipment Specifications",
    1: "Electrical & Instrumentation Documents",
    2: "Chemical Data & Water Analysis Reports",
    3: "Miscellaneous Data & Placeholders",
    4: "Project Proposals, Contracts & Financials",
    5: "Plant System Analysis & PFDs",
    6: "Engineering Drawings & Building Surveys",
    7: "Project Management & Planning Documents",
    8: "Controlled Drawings & Plot Files",
    9: "Water Treatment Systems & Planning"
}

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect to DB and Update Cluster Names ---
session = None
engine = None
action_performed = False

print("\nConnecting to database to update cluster names...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check import succeeded
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # Prepare the UPDATE statement once
        query_update = text("""
            UPDATE public.summary_vectors
            SET cluster_name = :cluster_name
            WHERE cluster_id = :cluster_id;
        """)

        print("\nUpdating cluster names in the database...")
        update_start_time = time.time()
        updated_clusters = 0

        # Loop through the mapping and execute update for each cluster
        for cluster_id, cluster_name in cluster_id_to_name.items():
            try:
                print(f"  Updating rows for Cluster ID {cluster_id} to Name: '{cluster_name}'...")
                result = session.execute(query_update, {
                    'cluster_name': cluster_name,
                    'cluster_id': cluster_id
                })
                # result.rowcount often indicates rows affected (driver dependent)
                print(f"    Rows matched (approx.): {result.rowcount}")
                updated_clusters += 1
                action_performed = True # Mark that we attempted an update
            except Exception as update_error:
                 warnings.warn(f"⚠️ Error updating name for Cluster ID {cluster_id}: {update_error}")
                 # Decide whether to continue or stop on error
                 # raise # Uncomment to stop on first error

        # Commit the entire transaction after all updates are executed
        if action_performed:
             print("\nCommitting all cluster name updates...")
             session.commit()
             print(f"   ✅ Cluster names committed for {updated_clusters} cluster IDs.")
             print(f"   Total update time: {time.time() - update_start_time:.2f}s")
        else:
             print("   No update actions were performed.")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    # Catch errors during connection or the main loop setup
    print(f"\n❌ An error occurred during the cluster name update process: {e}")
    if session:
        print("   Rolling back transaction due to error.")
        session.rollback()
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Cluster name update process finished.")

# %% [markdown]
# ## Next Steps
#
# 1. The `cluster_name` column in `summary_vectors` should now be populated with the descriptive names.
# 2. You can run a final verification cell or query the database directly to confirm.
# 3. The data is now fully prepared (basic info, embeddings, cluster ID, cluster name) for visualization or other downstream analysis. You can re-run the visualization script (Step 9) and modify it to show the `cluster_name` in the hover data or legend.



✅ init_vector_db imported successfully.

Connecting to database to update cluster names...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

Updating cluster names in the database...
  Updating rows for Cluster ID 0 to Name: 'Plant Utilities & Equipment Specifications'...
    Rows matched (approx.): 1465
  Updating rows for Cluster ID 1 to Name: 'Electrical & Instrumentation Documents'...
    Rows matched (approx.): 982
  Updating rows for Cluster ID 2 to Name: 'Chemical Data & Water Analysis Reports'...
    Rows matched (approx.): 601
  Updating rows for Cluster ID 3 to Name: 'Miscellaneous Data & Placeholders'...
    Rows matched (approx.): 907
  Updating rows for Cluster ID 4 to Name: 'Project Proposals, Contracts & Financials'...
    Rows matched (approx.): 1035
  Updating rows for Cluster ID 5 to Name: 'Plant System Analysis & PFDs'...
    Rows matched (approx.): 1197
  Updating rows for Cluster ID 6 to Name: 'Engineering Drawings & Building Surveys'...
    Rows matc

In [96]:
# %% [markdown]
# ## Step 12: Verify Cluster Name Population
#
# This final verification cell checks the `summary_vectors` table to confirm
# that the `cluster_name` column has been populated correctly based on the
# `cluster_id`, using the mapping defined in Step 11.

# %%
import sys
import time
import pandas as pd
from sqlalchemy import text, inspect as sql_inspect
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
SAMPLE_SIZE = 20 # How many rows to fetch for verification display (increase if needed)

# --- Cluster Name Mapping (Should match Step 11) ---
# Define the names for each cluster ID to verify against
cluster_id_to_name_expected = {
    0: "Plant Utilities & Equipment Specifications",
    1: "Electrical & Instrumentation Documents",
    2: "Chemical Data & Water Analysis Reports",
    3: "Miscellaneous Data & Placeholders",
    4: "Project Proposals, Contracts & Financials",
    5: "Plant System Analysis & PFDs",
    6: "Engineering Drawings & Building Surveys",
    7: "Project Management & Planning Documents",
    8: "Controlled Drawings & Plot Files",
    9: "Water Treatment Systems & Planning"
}

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Connect and Verify Data ---
session = None
engine = None
df_sample = pd.DataFrame() # Initialize empty DataFrame

print("\nConnecting to database to verify 'summary_vectors' cluster name population...")
connect_start_time = time.time()

try:
    if 'init_vector_db' in globals(): # Check import succeeded
        session, engine = init_vector_db(wipe_database=False)
        inspector = sql_inspect(engine)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Check Table Existence and Row Count ---
        print("\n[1/3] Checking table existence and row count...")
        if inspector.has_table("summary_vectors", schema="public"):
            print("   ✅ Table 'public.summary_vectors' exists.")
            count_result = session.execute(
                 text("SELECT COUNT(*) FROM public.summary_vectors;")
             ).scalar_one_or_none()
            row_count = count_result if count_result is not None else 0
            print(f"   📊 Current row count: {row_count}")

            # Check count of non-NULL cluster_names
            count_non_null_names = session.execute(
                text("SELECT COUNT(*) FROM public.summary_vectors WHERE cluster_name IS NOT NULL;")
            ).scalar_one_or_none()
            print(f"   📊 Rows with non-NULL cluster_names: {count_non_null_names or 0}")


            if row_count > 0 and (count_non_null_names or 0) > 0:
                # --- 2) Fetch Sample Data ---
                print(f"\n[2/3] Fetching {SAMPLE_SIZE} sample rows for name verification...")
                try:
                    # Get current column names to build query dynamically
                    columns_info = inspector.get_columns("summary_vectors", schema="public")
                    existing_columns = [col['name'] for col in columns_info] if columns_info else []
                    required_cols = ['doc_id', 'cluster_id', 'cluster_name']

                    if all(col in existing_columns for col in required_cols):
                        select_cols_str = ", ".join([f'"{col}"' for col in required_cols])
                        sample_query = text(f"""
                            SELECT {select_cols_str}
                            FROM public.summary_vectors
                            WHERE cluster_id IS NOT NULL AND cluster_name IS NOT NULL
                            ORDER BY doc_id -- Or RANDOM()
                            LIMIT :limit;
                        """)
                        df_sample = pd.read_sql(sample_query, con=engine, params={'limit': SAMPLE_SIZE})

                        if not df_sample.empty:
                            print(f"\n   📄 Sample data ({len(df_sample)} rows):")
                            display(df_sample) # Display DataFrame in notebook
                        else:
                             print("   ℹ️ Could not fetch sample rows with non-NULL cluster IDs and names.")
                    else:
                        missing_cols = [col for col in required_cols if col not in existing_columns]
                        print(f"   ❌ Required columns missing for verification: {', '.join(missing_cols)}.")

                except Exception as e:
                    print(f"   ⚠️ Error fetching sample data: {e}")

                # --- 3) Verify Names in Sample ---
                print("\n[3/3] Verifying cluster names in the sample...")
                if not df_sample.empty:
                    mismatches_found = 0
                    for index, row in df_sample.iterrows():
                        cluster_id = row['cluster_id']
                        actual_name = row['cluster_name']
                        expected_name = cluster_id_to_name_expected.get(cluster_id)

                        if expected_name is None:
                             print(f"   ⚠️ Row {index} (Doc ID {row['doc_id']}): Found unexpected cluster_id {cluster_id}. Cannot verify name.")
                             mismatches_found += 1
                        elif actual_name != expected_name:
                             print(f"   ❌ MISMATCH in Row {index} (Doc ID {row['doc_id']}): Cluster ID {cluster_id} has Name '{actual_name}', expected '{expected_name}'.")
                             mismatches_found += 1

                    if mismatches_found == 0:
                        print("   ✅ All cluster names in the sample match the expected names.")
                    else:
                        print(f"   ⚠️ Found {mismatches_found} mismatches/issues in the sample.")
                else:
                    print("   Skipping name verification as no sample data was fetched.")

            elif row_count > 0:
                 print("   ℹ️ Table has rows, but no non-NULL cluster names found.")
            else:
                print("   ℹ️ Table is empty. Cannot verify population.")
        else:
             print("   ❌ Table 'public.summary_vectors' does not exist. Cannot verify.")


    else:
        print("   Skipping database connection as init_vector_db was not imported.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred: {e}")
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Verification check finished.")

# %% [markdown]
# ## Pipeline Complete (Initial Version)
#
# 1. Review the verification results. Confirm that the cluster names in the sample match the expected names.
# 2. Your database table `summary_vectors` is now fully populated with basic info, embeddings, cluster IDs, and cluster names.
# 3. You can now use this data for further analysis, visualization (re-run Step 9 with modifications to show names), or other downstream tasks.



✅ init_vector_db imported successfully.

Connecting to database to verify 'summary_vectors' cluster name population...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.02s

[1/3] Checking table existence and row count...
   ✅ Table 'public.summary_vectors' exists.
   📊 Current row count: 9746
   📊 Rows with non-NULL cluster_names: 9746

[2/3] Fetching 20 sample rows for name verification...

   📄 Sample data (20 rows):


doc_id  cluster_id                                cluster_name
0        3           9          Water Treatment Systems & Planning
1        4           2      Chemical Data & Water Analysis Reports
2        5           8            Controlled Drawings & Plot Files
3        6           8            Controlled Drawings & Plot Files
4        7           8            Controlled Drawings & Plot Files
5        8           8            Controlled Drawings & Plot Files
6       10           0  Plant Utilities & Equipment Specifications
7       17           4   Project Proposals, Contracts & Financials
8       19           0  Plant Utilities & Equipment Specifications
9       20           4   Project Proposals, Contracts & Financials
10      22           3           Miscellaneous Data & Placeholders
11      24           0  Plant Utilities & Equipment Specifications
12      25           9          Water Treatment Systems & Planning
13      28           6     Engineering Drawings & Building Surveys
14      29           3           Miscellaneous Data & Placeholders
15      31           6     Engineering Drawings & Building Surveys
16      32           5                Plant System Analysis & PFDs
17      34           4   Project Proposals, Contracts & Financials
18      35           9          Water Treatment Systems & Planning
19      37           3           Miscellaneous Data & Placeholders


[3/3] Verifying cluster names in the sample...
   ✅ All cluster names in the sample match the expected names.

Database session closed.

✅ Verification check finished.


In [99]:
# %% [markdown]
# ## Step 13: Visualize Clusters using t-SNE (with Cluster Names)
#
# This cell fetches the embeddings and their assigned cluster names from the database,
# performs t-SNE dimensionality reduction on the embeddings (reducing them to 2D),
# and creates an interactive scatter plot to visualize the clusters, colored and
# labeled by their descriptive names.

# %%
import sys
import time
import pandas as pd
import numpy as np
import ast # For safely evaluating string representations of lists
from sqlalchemy import text, inspect as sql_inspect
from sklearn.manifold import TSNE # For t-SNE dimensionality reduction
import plotly.express as px
import plotly.io as pio
import warnings

# --- Configuration ---
# Adjust this path to point to your VDB pipeline location
VDB_PIPELINE_PATH = "/shared_folders/team_1/mark_vdb/vdb_pipeline" #<-- ADJUST IF NEEDED
EXPECTED_DIMENSION = 384 # Should match the embedding dimension
RANDOM_STATE = 42 # For reproducible t-SNE results
# t-SNE Parameters (can be tuned)
TSNE_PERPLEXITY = 30  # Typical value, relates to local neighborhood size
TSNE_ITERATIONS = 300 # Number of optimization iterations (increase for potentially better layout, but slower)
TSNE_COMPONENTS = 2   # Reduce to 2 dimensions for plotting

# --- Add VDB pipeline to Python path ---
if VDB_PIPELINE_PATH not in sys.path:
    sys.path.append(VDB_PIPELINE_PATH)

# --- Import database initializer ---
try:
    from init_vector_db import init_vector_db
    print("✅ init_vector_db imported successfully.")
except ImportError as e:
    warnings.warn(f"⚠️ Failed to import init_vector_db. Check VDB_PIPELINE_PATH: {e}")

# --- Import Scikit-learn and Plotly ---
try:
    from sklearn.manifold import TSNE
    print("✅ Scikit-learn (TSNE) imported successfully.")
except ImportError:
     warnings.warn("⚠️ Failed to import scikit-learn. Install it: pip install scikit-learn")

try:
    import plotly.express as px
    import plotly.io as pio
    # Set default renderer for notebooks (or use 'browser', 'vscode', etc.)
    pio.renderers.default = "plotly_mimetype+notebook_connected"
    print("✅ Plotly imported successfully.")
except ImportError:
     warnings.warn("⚠️ Failed to import Plotly. Install it: pip install plotly")


# --- Connect, Fetch, Parse, Reduce Dimensions, and Plot ---
session = None
engine = None
embedding_matrix = None # To hold the numerical embeddings
df_plot = pd.DataFrame() # To hold data for plotting

print("\nConnecting to database to fetch data for visualization...")
connect_start_time = time.time()

try:
    # Check if necessary libraries are available
    if 'init_vector_db' in globals() and 'TSNE' in globals() and 'px' in globals():
        session, engine = init_vector_db(wipe_database=False)
        print(f"   Connected in {time.time() - connect_start_time:.2f}s")

        # --- 1) Fetch Embeddings, Cluster Names, and Summaries ---
        fetch_start_time = time.time()
        print("\n[1/4] Fetching embeddings, cluster names, and summaries...")
        # Fetch all necessary columns, including cluster_name
        query_select = text("""
            SELECT doc_id, embedding, cluster_id, cluster_name, summary
            FROM public.summary_vectors
            WHERE embedding IS NOT NULL AND cluster_name IS NOT NULL; -- Fetch rows with names
        """)
        # Fetch all results into a DataFrame
        df_plot = pd.read_sql(query_select, con=engine)
        print(f"   Fetched {len(df_plot)} records in {time.time() - fetch_start_time:.2f}s")

        if not df_plot.empty:
            # --- 2) Parse Embeddings ---
            parse_start_time = time.time()
            print("\n[2/4] Parsing embeddings...")
            parsed_embeddings_list = []
            valid_indices = [] # Keep track of indices of valid rows in df_plot
            skipped_rows = 0

            for index, embedding_raw in df_plot['embedding'].items():
                parsed_embedding = None
                if isinstance(embedding_raw, str):
                    try:
                        parsed_embedding = ast.literal_eval(embedding_raw)
                        if isinstance(parsed_embedding, list) and len(parsed_embedding) == EXPECTED_DIMENSION:
                             parsed_embeddings_list.append(parsed_embedding)
                             valid_indices.append(index) # Store original DataFrame index
                        else:
                             skipped_rows += 1
                    except (ValueError, SyntaxError):
                        skipped_rows += 1
                else:
                    skipped_rows += 1

            if skipped_rows > 0:
                 warnings.warn(f"Skipped {skipped_rows} rows during embedding parsing.")

            if not parsed_embeddings_list:
                 raise ValueError("No valid embeddings could be parsed. Cannot proceed with visualization.")

            # Filter the DataFrame to only include rows with valid embeddings
            df_plot = df_plot.loc[valid_indices].copy()
            # Convert the list of lists into a NumPy matrix
            embedding_matrix = np.array(parsed_embeddings_list)
            print(f"   Parsed {len(df_plot)} valid embeddings into matrix shape: {embedding_matrix.shape}.")
            print(f"   Parsing finished in {time.time() - parse_start_time:.2f}s")

            # --- 3) Perform t-SNE Dimensionality Reduction ---
            tsne_start_time = time.time()
            print(f"\n[3/4] Performing t-SNE reduction ({embedding_matrix.shape[1]}D -> {TSNE_COMPONENTS}D)...")
            print(f"   (perplexity={TSNE_PERPLEXITY}, iterations={TSNE_ITERATIONS}) - This may take a while...")

            tsne = TSNE(n_components=TSNE_COMPONENTS,
                        perplexity=TSNE_PERPLEXITY,
                        n_iter=TSNE_ITERATIONS,
                        random_state=RANDOM_STATE,
                        metric='cosine', # Cosine distance often works well for high-dim text embeddings
                        n_jobs=-1) # Use all available CPU cores

            tsne_results = tsne.fit_transform(embedding_matrix)

            # Add t-SNE results to the DataFrame
            df_plot['tsne_1'] = tsne_results[:, 0]
            df_plot['tsne_2'] = tsne_results[:, 1]
            if TSNE_COMPONENTS == 3:
                df_plot['tsne_3'] = tsne_results[:, 2]

            print(f"   t-SNE finished in {time.time() - tsne_start_time:.2f}s")

            # --- 4) Create Interactive Plot ---
            plot_start_time = time.time()
            print("\n[4/4] Generating interactive plot using cluster names...")

            # Create a summary preview for hover
            df_plot['summary_preview'] = df_plot['summary'].str[:150] + '...'
            # Ensure cluster_name is treated as a category for consistent coloring
            df_plot['cluster_name'] = df_plot['cluster_name'].astype('category')

            plot_params = {
                'data_frame': df_plot,
                'x': 'tsne_1',
                'y': 'tsne_2',
                'color': 'cluster_name', # <<< Use cluster_name for color
                'hover_data': ['doc_id', 'summary_preview', 'cluster_name', 'cluster_id'], # <<< Show name and ID on hover
                'title': f'Document Clusters Visualization by Name (t-SNE)', # <<< Updated title
                'labels': {'tsne_1': 't-SNE Dimension 1', 'tsne_2': 't-SNE Dimension 2', 'cluster_name': 'Cluster Name'}, # <<< Label for legend
                'category_orders': {"cluster_name": sorted(df_plot['cluster_name'].unique())} # Consistent legend order by name
            }

            if TSNE_COMPONENTS == 3:
                plot_params['z'] = 'tsne_3'
                plot_params['labels']['tsne_3'] = 't-SNE Dimension 3'
                fig = px.scatter_3d(**plot_params)
            else:
                fig = px.scatter(**plot_params)

            # Improve layout and marker appearance
            fig.update_traces(marker=dict(size=5, opacity=0.7))
            fig.update_layout(margin=dict(l=0, r=0, b=0, t=40), legend_title_text='Cluster Name') # <<< Legend title

            # Display the plot
            fig.show()
            print(f"   Plotting finished in {time.time() - plot_start_time:.2f}s")


        else:
            print("   No records found with embeddings and cluster names. Cannot visualize.")

    else:
        print("   Skipping visualization because dependencies are missing.")

except Exception as e:
    print(f"\n❌ An unexpected error occurred during the visualization process: {e}")
    if session:
        session.rollback()
finally:
    # --- Close Connection ---
    if session and session.is_active:
        session.close()
        print("\nDatabase session closed.")

print(f"\n✅ Visualization attempt finished.")

# %% [markdown]
# ## Pipeline Complete!
#
# 1. Analyze the interactive plot. The points should now be colored based on the descriptive cluster names.
# 2. Hover over points to see the cluster name, ID, document ID, and summary preview.
# 3. This visualization provides the final "map" based on the pipeline we've built.



✅ init_vector_db imported successfully.
✅ Scikit-learn (TSNE) imported successfully.
✅ Plotly imported successfully.

Connecting to database to fetch data for visualization...
CHECKING IF SEARCH INDICES CREATED: True
   Connected in 0.01s

[1/4] Fetching embeddings, cluster names, and summaries...
   Fetched 9746 records in 0.20s

[2/4] Parsing embeddings...
   Parsed 9746 valid embeddings into matrix shape: (9746, 384).
   Parsing finished in 4.18s

[3/4] Performing t-SNE reduction (384D -> 2D)...
   (perplexity=30, iterations=300) - This may take a while...


/home/jonathan_morse/miniconda3/envs/ragui_env/lib/python3.13/site-packages/sklearn/manifold/_t_sne.py:1164: FutureWarning:

'n_iter' was renamed to 'max_iter' in version 1.5 and will be removed in 1.7.



   t-SNE finished in 5.49s

[4/4] Generating interactive plot using cluster names...


   Plotting finished in 0.10s

Database session closed.

✅ Visualization attempt finished.
